## Potentiaalikuoppa

Tämä on Jupyter-pohjainen 'notebook', joka käyttää Pythonia. 
Erityisesti koko työ on tehty numpy- ja matplotlib-pakettien avulla.
Näistä ensimmäinen mahdollistaa vektorilaskennan, kun taas jälkimmäisen tarkoitus on tuottaa vähällä vaivalla kuvia.

Käytät tätä 'notebookia' mahdollisesti osoitteessa colab.research.google.com. Colab on Googlen tarjoama pilvipalvelu koneoppimiseen, joten sen resurssit ovat moninkertaiset siihen, mitä me tarvitsemme.
Eräs bonus on, että Colab synkkaa automaattisesti Driven kanssa.

Ensimmäisen kerran koodia ajettaessa (pikanäppäin shift + enter) kestää pidempään kuin tavallisesti, koska vasta silloin Colab pyytää pilvipalvelun laskentaresursseja.
Vie joko hiiresi alhaalla olevan blokin päälle ja klikkaa ilmestyvää pyöreää nappia tai klikkaa blokkia ja paina shift + enter.


In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from google.colab import files # Tarvitaan kuvien tallentamiseen

plt.plot(np.linspace(-5,5,100),np.linspace(-5,5,100)**2)

Olettaen, että eteesi ilmestyi graafi paraabelista, Colab vaikuttaa toimivan ja sinulle on varattu joksikin aikaa laskentaresursseja Googlen palvelimelta (paitsi jos ajat tätä lokaalisti, missä tapauksessa onnittelut pakettien asentamisesta ja Jupiterin käyttöönotosta).

Seuraavaksi määritellään funktio, jolla voidaan valita potentiaalifunktio Schrödingerin yhtälöön, äärettömän kuopan sisälle. Ajatuksena tässä on, että potentiaalifunktiolle annetun vektorin ulkopuolella potentiaali on ääretön. Määritelmän alapuolella näkyy käyttöesimerkki.

In [ ]:
# model on tässä potentiaalin muodon nimi
# Palauttaa muotoa vastaavan funktion, jolle voi antaa argumentiksi vektorin
def potential(model):
    def V(x):
        if model == 'step':
            retval = np.heaviside(x,0.5)
        if model == 'harmonic':
            retval = 0.5*x**2
        if model == 'empty':
            retval = 0*x
        try:
            return retval
        except:
            raise Exception('Your potential name is not correct. Options are '
                            + 'currently: step, harmonic or empty. You wrote: ' 
                            + model)
    return V

Vtest = potential('step')
print(Vtest(0)) # Huomaa heaviside-funktion määritelmä nollassa
print(Vtest(np.array([-2,0,1])))
x = np.linspace(-3,3,100)
plt.plot(x,Vtest(x))
plt.xlabel(r'$x$')
plt.ylabel('Potentiaali')

Ratkaistaan sitten Schrödingerin yhtälöä sellaisissa yksiköissä, joissa $\hbar = 1$ ja $m = 1$, eli
$$ \left(-\frac{1}{2}\frac{\partial^2}{\partial x^2}+V(x)\right)\psi(x) = E \psi(x), \quad \psi(x = \pm L/2) = 0$$

Oletetaan nyt, että tietäisimme energian $E$, muttemme aaltofunktiota $\psi$.
Schrödingerin yhtälö on sitten toisen asteen differentiaaliyhtälö.
On mahdollista käyttää diskretisointia toiselle derivaatalle, mikä on erityisen järkevää esimerkiksi moniulotteisissa osittaisdifferentiaaliyhtälöissä (esim. aaltoyhtälö).
Tutustutaan tässä työssä kuitenkin ensimmäisen asteen differentiaaliyhtälöiden ratkaisuun, koska menetelmät (niin numeeriset kuin teoreettiset) ovat usein kehitetty niille.

Muunnos toisesta asteesta ensimmäiseen ei ole ajatuksen tasolla monimutkainen.
Otetaan aaltofunktion $\psi(x)$ lisäksi muuttujaksi sen paikkaderivaatta $\psi'(x) = d \psi(x)/dx$.
Merkitään selvyyden vuoksi kuitenkin $\phi(x) \equiv \psi'(x)$.
Jos ajatellaan, että $\phi$ on muuttuja, sen dynamiikka määräytyy aaltofunktiosta $\psi$; toisaalta $\psi$:n dynamiikka määräytyy $\phi$:stä.
Käyttämällä näitä symboleita voidaan kirjoittaa siis yhtälöpari
\begin{align}
    \phi'(x) &= 2(V(x) - E)\psi(x),\\
    \psi'(x) &= \phi(x).
\end{align}
''Lisäämällä'' muuttuja voitiin siis poistaa yksi aste derivaatasta.
Lineaarialgebran kielellä, joka on numeerisen laskennan perusta, voidaan kirjoittaa
$$
   \frac{d}{dx} \left(\begin{matrix} \psi \\ \phi \end{matrix}\right)
   = \left(\begin{matrix} 0 & 1 \\ 2(V(x) - E) & 0\end{matrix}\right) 
   \left(\begin{matrix} \psi \\ \phi \end{matrix}\right).
$$
Nyt voidaan soveltaa suoraviivaisesti yksi-ulotteisia menetelmiä ensimmäisen asteen differentiaaliyhtälön ratkaisuun kuten esimerkiksi Eulerin menetelmää tai Runge-Kutta menetelmiä.

Alla on käytetty Eulerin menetelmää. Jos kirjoitetaan yllä oleva yhtälö yksinkertaisesti $f'(x) = A(x) f(x)$, Eulerin menetelmä voidaan johtaa käyttämällä Taylorin sarjakehitelmää tuntemattomalle funktiolle $f(x)$ pienen askeleen $\Delta x$ avulla
\begin{align}
				f(x + \Delta x) &= \sum_{n = 0}^{\infty} \frac{1}{n!} f^{(n)}(x) (\Delta x)^{n}  \\
				&= f(x) + f'(x)\Delta x + \mathcal{O}((\Delta x)^2)\\
					&\approx f(x) + f'(x) \Delta x \\
          &=  f(x) + A(x) f(x) \Delta x.
\end{align}
Nyt voidaan siis laskea funktion $f(x + \Delta x)$ arvoja, kunhan tiedetään $f(x)$ arvo sekä etutekijän $A(x)$ arvo.
Huomaa, että johdossa tehtiin approksimaatio, kun Taylorin sarja katkaistiin: seurauksena numeerista virhettä.

Tarvitaan kuitenkin vielä alkuehdot differentiaaliyhtälölle, jotta voidaan käyttää Eulerin menetelmää.
Tiedetään, että Schrödingerin yhtälölle on kaksi reunaehtoa: aaltofunktio katoaa laatikon reunoilla eli $\psi(\pm L/2) = 0$.
Ainoa tapa päästä eteenpäin on valita jokin derivaatan alkuehto.
Valitaan siis $\psi(- L/2) = 0$ ja esimerkiksi $\psi'(-L/2) = 1$, vaikkei tämä alkuehto olisikaan oikein.

Nyt siis voidaan ratkaista Schrödingerin yhtälöä annetulla energialla ja arvatulla reunaehdolla.

In [ ]:
# Schrödingerin yhtälön näköisen differentiaaliyhtälön ratkaisin annetulla energialla
# Argumentteina energia E, potentiaalifunktio Vf (ks. käyttöesimerkki), ja paikkavektori xs. 
def wf_solver(E,Vf,xs):
    y = np.zeros((2,np.size(xs)))
    
    y[0,0] = 0
    y[1,0] = 1
    
    # Eulerin menetelmä
    V = Vf(xs)
    for k in range(1,np.size(xs)):
        A = np.array([[0,1],[2*(V[k]-E),0]])
        y[:,k] = y[:,k-1] + (xs[k] - xs[k-1])*np.dot(A,y[:,k-1])

    return wf_norm(y[0,:],xs)

# Normittaa funktion wf(x) neliön integraalin ykköseksi
def wf_norm(wf,x):
    wf2 = np.abs(wf)**2
    norm = np.sum((wf2[1:] + wf2[:-1])*(x[1:] - x[:-1]))/2
    return wf/np.sqrt(norm)

# Testataan solveria energia-arvolla E = 1
plt.plot(np.linspace(-5,5,1000),
         wf_solver(1,potential('empty'),np.linspace(-5,5,1000)))
plt.xlabel(r'$x$')
plt.ylabel('Pseudo-aaltofunktio')

Viimeinen askel energian $E$ ratkaisuun on hyödyntää reunaehtoa äärettömän syvän kuopan toisessa päässä eli $\psi(L/2) = 0$. 
Ongelma on sama kuin klassinen (ja väkivaltainen) esimerkki tykin suuntaamisesta kohteeseen tasamaalla: tykin kulman sijasta muutetaankin energiaa $E$ siten, että aaltofunktio katoaa toisessa reunassa.

Algoritmi on seuraava: Annetaan kaksi energia-arvoa, joista toisella aaltofunktio on päätepisteessä negativiinen ja toisella positiivinen.
Koska päätepiste energian funktiona on jatkuva, tiedetään, että täytyy olla olemassa jokin energia-arvo, jolla aaltofunktio katoaa.
Sitten voidaan valita näiden energia-arvojen keskeltä uusi energia, ja katsoa minkä merkin aaltofunktio saa päätepisteessä.
Näin saatiin puolitettua energiaväli.
Toistamalla tätä saadaan energia ratkaistua halutulla tarkkuudella.

In [ ]:
# Apufunktio, joka ratkaisee Schöringerin yhtälön annetulla potentiaalilla
# sekä energialla ja palauttaa aaltofunktion arvon päätepisteessä.
# Energia voidaan antaa joko vektorina tai yksittäisenä arvona
def wf_endvalue(E,V,x):
    if np.size(E) > 1:
        retval = np.zeros(np.size(E))
        k=0
        for Eval in E:
            retval[k] = wf_solver(Eval,V,x)[-1]
            k += 1
    else:
        retval = wf_solver(E,V,x)[-1]
    return retval

In [ ]:
# Energian etsintä puolitusmenetelmällä
# Annetaan energian ala- ja ylärajat Emin ja Emax sekä haluttu ratkaisutarkkuus acc
# V ja x kuten edellä potentiaalifunktio ja paikkavektori
def energy_iteration(Emin,Emax,V,x,acc):
    wf_minval = wf_endvalue(Emin,V,x)
    wf_maxval = wf_endvalue(Emax,V,x)
    
    # Energia-arvauksien järkevyys pitää tarkistaa
    if np.sign(wf_minval*wf_maxval) == 1:
        raise Exception('Does not converge because of initial values!')
    
    # Pidetään huoli siitä, että Emin vastaa tästä lähtien 
    # päätepisteen negatiivista aaltofunktion arvoa
    if wf_minval > 0:
        tmp = Emin
        Emin = Emax
        Emax = tmp
    
    while True:
        E = (Emin + Emax)/2
        if np.abs(Emin - Emax)/2 < acc:
            return E
        
        wf_tempval = wf_endvalue(E,V,x)
        
        if wf_tempval < 0:
            Emin = E
        else:
            Emax = E

**Tässä kohtaa pallo siirtyy teille**: Kaikki funktiot, joita tarvitaan äärettömän syvän tasapohjaisen ja porraspohjaisen potentiaalikuopan ominaisenergioiden ja aaltofunktioiden ratkaisemiseen, on esitelty.

Ensimmäisenä voi olla hyvä ja palata vähän taaksepäin ja kerrata numeeriset vaiheet. Erityisesti, emme missään vaiheessa palanneet muokkaamaan Eulerin menetelmälle antamaamme derivaatan alkuarvausta. Miksi? Oliko arvaus oikein ja vastaus yksi?

Yksi tapa tehdä työtä on vain vaihtaa energia-arvauksia, etsien ensin alimman tilan energian, siirtyen siitä seuraavaan ja niin edelleen, kunnes kahdeksan alinta tilaa on löydetty.
On hyvä muistaa, että aaltofunktion muoto kertoo, kuinka mones tila on kyseessä.
Alimmalla tilalla on yksi kupu, toiseksi alimmalla kaksi kupua ja niin edelleen.

In [ ]:
# Kuopan leveys
L = 20
# Kuinka moneen osaan kuopan sisäinen väli jaetaan
intervals = 1000

xs = np.linspace(-L/2,L/2,intervals)

# Kaksi eri esimerkkiä
Vempty = potential('empty')
Vstep = potential('step')

Eval1 = energy_iteration(0, 0.04, Vempty,xs,1e-9)
print("Löydetty energian arvo tasapohjaiselle: ", Eval1)

Eval2 = energy_iteration(0, 0.1, Vstep,xs,1e-9)
print("Löydetty energian arvo porraspohjaiselle: ", Eval2)

In [ ]:
# Piirretään sitten edellä löydettyjä energioita vastaavat aaltofunktiot

plt.plot(xs, wf_solver(Eval1,Vempty,xs), 'b')
plt.plot(xs, wf_solver(Eval2,Vstep,xs), 'r:')

plt.xlabel(r'$x$') 
plt.ylabel(r'$\psi(x)$')

# On mahdollista myös tallentaa kuvat omalle koneelle
#plt.savefig("testi.pdf")
#files.download("testi.pdf")

Käsitellään vielä lyhyesti numeerista virhettä, johon viitattiin Eulerin menetelmän johdossa. Toinen virhelähde numeerisesti tulee siitä, että on valittava pienin väli energiaiteraatiolle (koodissa ''acc''). Mitä eroa näillä on ja kumpi on merkittävämpi?

Differentiaaliyhtälön ratkaisijoita luokitellaan sen mukaan, monenteenko potenssiin ratkaisun virhe riippuu askelkoosta. 
Eulerin menetelmä on ensimmäisen asteen menetelmä, eli ratkaisun virhe on verrannollinen askelkoon ensimmäiseen potenssiin.
Huomaa kuitenkin, että yhden askeleen virhe menee askelkoon toiseen potenssiin.
Tämä ero johtuu siitä, että askeleita pitää ottaa noin (välin pituus)/(askelkoko) verran.
Virheen riippuvuuden askelkoosta näkee helposti seuraavasta esimerkistä.
On olemassa tarkempia algoritmeja, joista mainio esimerkki ovat nk. [Runge-Kutta menetelmät](https://mathworld.wolfram.com/Runge-KuttaMethod.html), joihin voit halutessasi tutustua.

In [ ]:
# Valitaan nyt jokin eksakti ratkaisu ja verrataan sitä kahteen numeeriseen
# ratkaisuun eri askelväleillä

# Eksakti ratkaisu mustalla, energia np.pi**2*3**2/(2*10**2)
x = np.linspace(-5,5,1000)
plt.plot(x, -np.sqrt(2/10)*np.cos((3*np.pi/10)*x),'k')

# Pienempi askelkoko sinisellä katkoviivalla
x = np.linspace(-5,5,400)
plt.plot(x, wf_solver(np.pi**2*3**2/(2*10**2),potential('empty'),x),'b--')

# Suurempi askelkoko punaisella pisteviivalla
x = np.linspace(-5,5,50)
plt.plot(x, wf_solver(np.pi**2*3**2/(2*10**2),potential('empty'),x),'r:')

plt.xlabel(r'$x$') 
plt.ylabel(r'$\psi(x)$')